# 01_create_proximeta_master_table

This script creates a master table for all proximeta data (contigs and vmags) with columns for all of the information available in google drive.

In [4]:
# Load packages
import pandas as pd
import os
import os.path as op
import sys
import csv
import numpy as np
import matplotlib
import glob
import seaborn as sns
from collections import Counter
import matplotlib.pyplot as plt

# file paths
path = '/Users/melissaherring/Google Drive/My Drive/MH_project/'
#path = '/Users/juliabrown/Google Drive/My Drive/projects/OMZvir_round2/MH_project/'

# define functions 
def split_classification(df):
    df[['domain','phyla','class','order','family','genus','species']] = df.classification.str.split(';', expand=True)
    df['domain'] = df['domain'].str.replace('d__', '')
    df['phyla'] = df['phyla'].str.replace('p__', '')
    df['class'] = df['class'].str.replace('c__', '')
    df['order'] = df['order'].str.replace('o__', '')
    df['family'] = df['family'].str.replace('f__', '')
    df['genus'] = df['genus'].str.replace('g__', '')
    df['species'] = df['species'].str.replace('s__', '')
    return df
def split_contig_id(df):
    df['virus_name'] = df['contig_id'].str.split("|").str[0]
    df['N'] = pd.to_numeric(df['contig_id'].str.split("|").str[1].str.replace('N=', ''))
    df['L'] = pd.to_numeric(df['contig_id'].str.split("|").str[2].str.replace('L=', ''))
    return df

# global options
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)


''' JOIN ASSOCIATED CONTIG AND VMAG DATA '''


# input contig data
jv119_contig = pd.read_csv(op.join(path,'data/proximeta_viral_files/jv-119_proximeta/viral_hosts/viral_host_associations_filtered.tsv'), sep ='\t')
jv121_contig = pd.read_csv(op.join(path,'data/proximeta_viral_files/jv-121_proximeta/viral_hosts/viral_host_associations_filtered.tsv'), sep ='\t')
jv132_contig = pd.read_csv(op.join(path,'data/proximeta_viral_files/jv-132_proximeta/viral_hosts/viral_host_associations_filtered.tsv'), sep ='\t')
jv154_contig = pd.read_csv(op.join(path,'data/proximeta_viral_files/jv-154_proximeta/viral_hosts/viral_host_associations_filtered.tsv'), sep ='\t')

# create a list of all contig dataframes
contig_list = [jv119_contig, jv121_contig, jv132_contig, jv154_contig]

# input vMAG data
jv119_vmag = pd.read_csv(op.join(path,'data/proximeta_viral_files/jv-119_proximeta/vMag_hosts/vMAG_host_associations_filtered.tsv'), sep ='\t')
jv121_vmag = pd.read_csv(op.join(path,'data/proximeta_viral_files/jv-121_proximeta/vMag_hosts/vMAG_host_associations_filtered.tsv'), sep ='\t')
jv132_vmag = pd.read_csv(op.join(path,'data/proximeta_viral_files/jv-132_proximeta/vMag_hosts/vMAG_host_associations_filtered.tsv'), sep ='\t')
jv154_vmag = pd.read_csv(op.join(path,'data/proximeta_viral_files/jv-154_proximeta/vMag_hosts/vMAG_host_associations_filtered.tsv'), sep ='\t')

# create a list of all vmag dataframes
vmag_list = [jv119_vmag, jv121_vmag, jv132_vmag, jv154_vmag]

# create virus_type column for each dataframe
for df in contig_list:
    df['virus_type'] = 'contig'
for df in vmag_list:
    df['virus_type'] = 'vmag'

# rename columns to match betweeen contig and vmag dataframes

## create dictionaries to use for column mapping -> old_col_name : new_col_name
column_mapping_contig = {
    'mobile_contig_name': 'virus_name',
    'mobile_contig_length (bp)': 'virus_length',
    'mobile_contig_read_count (reads)': 'virus_read_count',
    'mobile_contig_read_depth (reads/kbp)': 'virus_read_depth',
    'mobile_contig_read_depth_in_this_cluster (reads/kbp)': 'virus_read_depth_in_host',
    'cluster_name': 'host_name',
    'cluster_length (bp)': 'host_length',
    'cluster_read_count (reads)': 'host_read_count',
    'cluster_read_depth (reads/kbp)': 'host_read_depth',
    'intra_read_count (reads)': 'intra_read_count',
    'intra_linkage_density (reads/kbp^2)': 'intra_linkage_density',
    'inter_read_count (reads)': 'inter_read_count',
    'raw_inter_linkage_density (reads/kbp^2)': 'raw_inter_linkage_density',
    'raw_inter_vs_intra_ratio': 'raw_inter_vs_intra_ratio',
    'mobile_element_copies_per_cell': 'viral_copies_per_cell',
    'adjusted_inter_connective_linkage_density (reads/kbp^2)': 'adjusted_inter_linkage_density',
    'adjusted_inter_vs_intra_ratio': 'adjusted_inter_vs_intra_ratio',
    'sample_name':'sample_name',
    'virus_type': 'virus_type',
    'sample_depth': 'sample_depth'
}
column_mapping_vmag = {
    'mobile_cluster_name': 'virus_name',
    'mobile_cluster_length (bp)': 'virus_length',
    'mobile_cluster_read_count (reads)': 'virus_read_count',
    'mobile_cluster_read_depth (reads/kbp)': 'virus_read_depth',
    'mobile_cluster_read_depth_in_this_cluster (reads/kbp)': 'virus_read_depth_in_host',
    'cluster_name': 'host_name',
    'cluster_length (bp)': 'host_length',
    'cluster_read_count (reads)': 'host_read_count',
    'cluster_read_depth (reads/kbp)': 'host_read_depth',
    'intra_read_count (reads)': 'intra_read_count',
    'intra_linkage_density (reads/kbp^2)': 'intra_linkage_density',
    'inter_read_count (reads)': 'inter_read_count',
    'raw_inter_linkage_density (reads/kbp^2)': 'raw_inter_linkage_density',
    'raw_inter_vs_intra_ratio': 'raw_inter_vs_intra_ratio',
    'mobile_element_copies_per_cell': 'viral_copies_per_cell',
    'adjusted_inter_connective_linkage_density (reads/kbp^2)': 'adjusted_inter_linkage_density',
    'adjusted_inter_vs_intra_ratio': 'adjusted_inter_vs_intra_ratio',
    'sample_name':'sample_name',
    'virus_type': 'virus_type',
    'sample_depth': 'sample_depth'
}

## for loops to rename columns
for df in contig_list:
    df.rename(columns=column_mapping_contig, inplace=True)
for df in vmag_list: 
    df.rename(columns=column_mapping_vmag, inplace=True)
    
# create sample_name, sample_depth column, and cluster_name for each dataframe
for df in list([jv119_contig, jv119_vmag]):
    df['sample_name'] = 'JV119'
    df['sample_depth'] = 400
    df['host_name'] = 'JV119_' + df['host_name']
for df in list([jv121_contig, jv121_vmag]):
    df['sample_name'] = 'JV121'
    df['sample_depth'] = 95
    df['host_name'] = 'JV121_' + df['host_name']
for df in list([jv132_contig, jv132_vmag]):
    df['sample_name'] = 'JV132'
    df['sample_depth'] = 80
    df['host_name'] = 'JV132' + df['host_name']
for df in list([jv154_contig, jv154_vmag]):
    df['sample_name'] = 'JV154'
    df['sample_depth'] = 140
    df['host_name'] = 'JV154_' + df['host_name']

# merge all contig and vmag dataframes together
proximeta = pd.concat([jv119_contig, jv121_contig, jv132_contig, jv154_contig, jv119_vmag, jv121_vmag, jv132_vmag, jv154_vmag])

''' MERGE MAG GTDB DATA TOGETHER '''


# input mag gtdb files
jv119_arc = pd.read_csv(op.join(path,'data/mag_data/jv-119_gtdbtk/jv-119.ar53.summary.tsv'),sep='\t')
jv119_bac = pd.read_csv(op.join(path,'data/mag_data/jv-119_gtdbtk/jv-119.bac120.summary.tsv'),sep='\t')
jv121_arc = pd.read_csv(op.join(path,'data/mag_data/jv-121_gtdbtk/jv-121.ar53.summary.tsv'),sep='\t')
jv121_bac = pd.read_csv(op.join(path,'data/mag_data/jv-121_gtdbtk/jv-121.bac120.summary.tsv'),sep='\t')
jv132_arc = pd.read_csv(op.join(path,'data/mag_data/jv-132_gtdbtk/jv-132.ar53.summary.tsv'),sep='\t')
jv132_bac = pd.read_csv(op.join(path,'data/mag_data/jv-132_gtdbtk/jv-132.bac120.summary.tsv'),sep='\t')
jv154_arc = pd.read_csv(op.join(path,'data/mag_data/jv-154_gtdbtk/jv-154.ar53.summary.tsv'),sep='\t')
jv154_bac = pd.read_csv(op.join(path,'data/mag_data/jv-154_gtdbtk/jv-154.bac120.summary.tsv'),sep='\t')

# create sample_name and sample_depth column for each mag gtdb dataframe
for df in list([jv119_arc, jv119_bac]):
    df['sample_name'] = 'JV119'
    df['sample_depth'] = 400
    df['user_genome'] = 'JV119_' + df['user_genome']
for df in list([jv121_arc, jv121_bac]):
    df['sample_name'] = 'JV121'
    df['sample_depth'] = 95
    df['user_genome'] = 'JV121_' + df['user_genome']
for df in list([jv132_arc, jv132_bac]):
    df['sample_name'] = 'JV132'
    df['sample_depth'] = 80
    df['user_genome'] = 'JV132_' + df['user_genome']
for df in list([jv154_arc, jv154_bac]):
    df['sample_name'] = 'JV154'
    df['sample_depth'] = 140
    df['user_genome'] = 'JV154_' + df['user_genome']
    
# combine all mag gtdb dataframes
mag_gtdb = pd.concat([jv119_arc, jv119_bac, jv121_arc, jv121_bac, jv132_arc, jv132_bac, jv154_arc, jv154_bac])

# split the classification into tax level columns and rename
mag_gtdb = split_classification(mag_gtdb)

''' MERGE PROXIMETA AND GTDB DATA '''


# rename mag_gtdb user_genome column to match proximeta dataframe
mag_gtdb.rename(columns={'user_genome':'host_name'}, inplace=True) 

# Merge two data frames together
proximeta_gtdb = proximeta.merge(mag_gtdb,how='outer',on=["host_name","sample_name","sample_depth"]).replace('', np.nan).fillna("NA")

# Replace NA with 'uninfected mag' (MAGs with no associated viruses)
proximeta_gtdb['virus_type'] = proximeta_gtdb['virus_type'].replace('NA', 'uninfected mag')

# input vmag summary files
jv119_vmag_sum = pd.read_csv(op.join(path,'data/proximeta_viral_files/jv-119_proximeta/viral_MAGs/viral_mags_summary.tsv'), sep = '\t')
jv121_vmag_sum = pd.read_csv(op.join(path,'data/proximeta_viral_files/jv-121_proximeta/viral_MAGs/viral_mags_summary.tsv'), sep = '\t')
jv132_vmag_sum = pd.read_csv(op.join(path,'data/proximeta_viral_files/jv-132_proximeta/viral_MAGs/viral_mags_summary.tsv'), sep = '\t')
jv154_vmag_sum = pd.read_csv(op.join(path,'data/proximeta_viral_files/jv-154_proximeta/viral_MAGs/viral_mags_summary.tsv'), sep = '\t')

# create sample_name column
jv119_vmag_sum['sample_name'] = 'JV119'
jv121_vmag_sum['sample_name'] = 'JV121'
jv132_vmag_sum['sample_name'] = 'JV132'
jv154_vmag_sum['sample_name'] = 'JV154'

# split up contig_id column into different columns
for df in list([jv119_vmag_sum,jv121_vmag_sum,jv132_vmag_sum,jv154_vmag_sum]):
    df = split_contig_id(df)
    
# combine all vmag summary dataframes together
vmag_sums = pd.concat([jv119_vmag_sum, jv121_vmag_sum, jv132_vmag_sum, jv154_vmag_sum])

# remove contig_id column and turn all empty observations to NA
vmag_sums = vmag_sums.drop('contig_id', axis=1).fillna("NA")

# merge with proximeta_gtdb
proximeta_sum = proximeta_gtdb.merge(vmag_sums,how='outer',on=["sample_name","virus_name"]).replace('', np.nan).fillna("NA")

# replace NA with unassociated vmag
proximeta_sum['virus_type'] = proximeta_sum['virus_type'].replace('NA', 'unassociated vmag')

proximeta_sum

virus_name virus_length virus_read_count virus_read_depth  \
0       k141_30505       6674.0             91.0        13.635001   
1     k141_4246884      10943.0            244.0        22.297359   
2     k141_3910817      15693.0            295.0         18.79819   
3     k141_4680690       8982.0            141.0        15.698063   
4     k141_6141634       5905.0            114.0        19.305673   
5     k141_3651856       8253.0            231.0        27.989822   
6     k141_7190536       8240.0            101.0        12.257282   
7     k141_4910956       5917.0            180.0        30.420821   
8     k141_2067012      15781.0            295.0        18.693365   
9           vMAG_1     116593.0           1993.0        17.093651   
10    k141_2024815       6453.0            100.0        15.496668   
11    k141_4832612       5184.0             64.0        12.345679   
12    k141_7022688       9957.0            143.0        14.361756   
13     k141_547779       5899.0             70.0        11.866418   
14         vMAG_26      16410.0            243.0        14.808044   
15     k141_554695       6107.0             49.0         8.023579   
16    k141_1736664       5100.0             17.0         3.333333   
17    k141_1008272       9439.0            446.0        47.250768   
18    k141_1047951       6415.0            321.0        50.038971   
19    k141_3683655       6043.0            161.0        26.642396   
20    k141_5480946      14065.0            617.0        43.867757   
21    k141_2878208       6018.0             80.0        13.293453   
22    k141_3753340       5007.0             93.0        18.573996   
23    k141_4328449       6714.0            112.0        16.681561   
24         vMAG_32      21616.0            791.0        36.593264   
25    k141_6059764       6451.0            776.0       120.291428   
26    k141_3188054       5136.0            516.0        100.46729   
27    k141_5705310       7255.0           1870.0       257.753274   
28    k141_6642169       5012.0             74.0        14.764565   
29    k141_1591692       6752.0            101.0        14.958531   
30    k141_3076273       5430.0            330.0        60.773481   
31    k141_6863216       5019.0            317.0        63.159992   
32     k141_497473       8264.0            470.0        56.873185   
33    k141_5765006       9332.0            377.0        40.398628   
34     k141_906079       5427.0            138.0        25.428413   
35    k141_1037796       7522.0            282.0        37.490029   
36    k141_1500180       8465.0            381.0         45.00886   
37         vMAG_10      21006.0            980.0        46.653337   
38    k141_6037317       6777.0           1945.0       287.000148   
39    k141_3712162       5603.0           1236.0       220.596109   
40    k141_3635793       6714.0            598.0         89.06762   
41    k141_6039814       5238.0            297.0        56.701031   
42    k141_1937066       6147.0           1375.0       223.686351   
43    k141_4705130      13803.0           1056.0        76.505108   
44    k141_1156191       5777.0            527.0        91.223819   
45    k141_5046790       6319.0            826.0       130.716886   
46         vMAG_11      11750.0           2611.0       222.212766   
47    k141_2384146       5034.0           3729.0       740.762813   
48    k141_6698691       5834.0           1709.0        292.93795   
49    k141_2840130      12262.0          11003.0       897.325069   
50    k141_3376092       7787.0           2654.0       340.824451   
51     k141_955648       9906.0           1666.0         168.1809   
52    k141_7202868       6174.0           2334.0       378.036929   
53    k141_2260297       6532.0           1643.0       251.530925   
54    k141_4470424      15375.0           8570.0       557.398374   
55    k141_5809684       5046.0           4683.0       928.061831   
56    k141_2629992       5309.0           1201.0       226.219627   
57    

In [ ]:
jv119 = proximeta_sum[proximeta_sum['sample_name'] == 'JV119']
jv119.to_csv(op.join(path, 'tables/jv119.csv'), index=False)

In [ ]:
proximeta_sum.to_csv(op.join(path, 'tables/proximeta_master.csv'), index=False)

In [ ]:
sorted_df = proximeta_sum.sort_values(by=['sample_name', 'virus_name'], ascending=[True, True])
sorted_df.to_csv(op.join(path, 'tables/proximeta_master.csv'), index=False)